In [1]:
from selenium import webdriver
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.support.ui import WebDriverWait # available since 2.4.0
from selenium.webdriver.support import expected_conditions as EC # available since 2.26.0

In [2]:
from bs4 import BeautifulSoup as bs
from splinter import Browser
import pandas as pd
import requests

In [3]:
import datetime as dt
import time as t

In [4]:
import numpy

In [5]:
from sqlalchemy import create_engine

In [6]:
from Candidates import candidates_list

In [107]:
driver = webdriver.Chrome()

In [9]:
candidates_info = candidates_list

In [38]:
# candidates_info

In [12]:
#Iterate through candidates
for candidate in candidates_info:
    
    #Create new key with empty list as value - to contain tweets
    candidate["tweets"] = []
    #Create base url
    url = candidate["twitter_url"]
    #Username is the last portion of url
    current_user = url[20:]
    
    #Extract announcment date, convert to datetime object and unix value
    current_announcement_date = candidate["announcement_date"]
    current_datetime = dt.datetime.strptime(current_announcement_date, "%B %d, %Y")
    current_utc = (current_datetime - dt.datetime(1970,1,1)).total_seconds()
    
    #Go to url
    driver.get(url)
    #Create variable which determines if the JS has generated the announcment tweet
    announcement_show = False
    #Variables to capture known bug
    bug_counter = 0
    bug_check = ""
    
    ######### While Loop to Scroll Page ############
    
    # Potential Bug - if last tweet on page happens to be an old retweet, prematurely stops scroll
    #As long as announcement tweet is not showing, we will scroll down the page
    while announcement_show == False:
        #Find all generated tweets
        stream_items = driver.find_elements_by_class_name("js-stream-item")
        #Find last generated tweet
        last_stream = stream_items[-1]
        
        # Some candidates began their twitter on the day of their announcement. This "bug check" will prevent endless while loop
        if last_stream.get_attribute("data-item-id") == bug_check:
            # If last tweet repeats itself, increase bug count
            bug_counter = bug_counter + 1
            print(bug_counter)
            # We give it 20 strikes, break the while loop if condition met
            if bug_counter == 20:
                announcement_show = True
            # Cushion to allow page to load
            t.sleep(5)
        # Reset counter if last tweet is new
        else:
            bug_counter = 0
        # Variable to check against when loop iterates again
        bug_check = last_stream.get_attribute("data-item-id")
        
        # Narrow selenium object to the header where username exists
        tweet = last_stream.find_element_by_class_name("tweet")
        content = tweet.find_element_by_class_name("content")
        header = content.find_element_by_class_name("stream-item-header")
    
        # Find the unix attribute contained within tweet and convert to int
        time_container = header.find_element_by_class_name("time")
        tweet_timestamp = time_container.find_element_by_class_name("tweet-timestamp")
        timestamp = tweet_timestamp.find_element_by_class_name("_timestamp")
        time_data = timestamp.get_attribute("data-time")
        time_data = int(time_data)
        
        # Compare announcment date unix to tweet unix
        # If the tweet unix exists before announcement unix, break loop - we have found all necessary tweets
        if time_data < current_utc:
            announcement_show = True
            break
        # Otherwise scroll
        else:
            driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")

    ########## Find  Tweets From User ##########
    # Emplty List to contain tweets
    tweet_list = []
    
    # Iterate through All Tweets
    for stream in stream_items:
        # Retreive Stream ID which is a part of the specific tweet url
        stream_id = stream.get_attribute("data-item-id")
        
        # Find username for each tweet
        tweet = stream.find_element_by_class_name("tweet")
        content = tweet.find_element_by_class_name("content")
        header = content.find_element_by_class_name("stream-item-header")
        account = header.find_element_by_class_name("account-group")
        username = account.find_element_by_class_name("username")
        username = username.text[1:]
        
        # If the tweet is from the current user, find unix time data
        if username == current_user:
            time_container = header.find_element_by_class_name("time")
            tweet_timestamp = time_container.find_element_by_class_name("tweet-timestamp")
            timestamp = tweet_timestamp.find_element_by_class_name("_timestamp")
            time_data = timestamp.get_attribute("data-time")
            time_data = int(time_data)
            
            # If tweet exists after the announcment date, append to tweet list
            if time_data > current_utc:
                #Debugging
                print("running")
                #Append list for driver.get to go to specific tweet urls
                tweet_list.append({
                    "stream_id": stream_id,
                    "data_time": time_data
                })
    # When finished, sort tweet list by datetime
    tweet_list.sort(key = lambda x:x["data_time"], reverse = True)

    ############# Iterate through User Tweets ###############
    for tweet in tweet_list:
        # Request specific tweet URL which contains relevant data
        stream_id = tweet['stream_id']
        tweet_url = url + "/status/" + stream_id
        driver.get(tweet_url)

        # Tweet Container
        tweet_container = driver.find_element_by_class_name("permalink-tweet")
        # Tweet Details which contains Datetime, Favorites and Retweets
        tweet_details = tweet_container.find_element_by_class_name("tweet-details-fixer")
        
        try:
            # Retrieve the datetime string and create variable which converts to datetime object
            datetime_container = tweet_details.find_element_by_class_name("client-and-actions")
            datetime_span = datetime_container.find_element_by_class_name("metadata")
            # Bug - some tweets contain "from {location}" after date time, need to narrow down to first sub span element
            datetime_sub_span = datetime_span.find_element_by_tag_name("span")
            tweet_date_string = datetime_sub_span.text
            tweet_date_datetime = dt.datetime.strptime(tweet_date_string, "%I:%M %p - %d %b %Y")
        except:
            print(f"Error! StreamID= {tweet_url}")
        
        # Stats Container contains Favorites and Retweets
        stats_container = tweet_details.find_element_by_class_name("js-tweet-stats-container")
        
        # Retrieve Retweets
        try:
            stats_ul = stats_container.find_element_by_class_name("stats")
            stat_retweets = stats_ul.find_element_by_class_name("js-stat-retweets")
            retweets_anchor = stat_retweets.find_element_by_class_name("request-retweeted-popup")
            retweets_count = retweets_anchor.text[:-9]
            retweets_count = int(retweets_count.replace(",", ""))
        except:
            retweets_count = 0

        # Retrieve Favorites
        try:
            stats_ul = stats_container.find_element_by_class_name("stats")
            stat_favorites = stats_ul.find_element_by_class_name("js-stat-favorites")
            favorites_anchor = stat_favorites.find_element_by_class_name("request-favorited-popup")
            favorites_count = favorites_anchor.text[:-6]
            favorites_count = int(favorites_count.replace(",", ""))
        except:
            favorites_count = 0

        # Retrieve Comments from Tweet Container
        try:
            tweet_footer = tweet_container.find_element_by_class_name("stream-item-footer")
            comments_container = tweet_footer.find_element_by_class_name("ProfileTweet-actionCount")
            comments_count = comments_container.get_attribute("data-tweet-stat-count")
            comments_count = int(comments_count)
        except:
            comments_count = 0
        
        # From comments, retweets, and favorites, generate an "engagement" score
        # Geometric mean takes the cubic root
        engagement_score = numpy.power((retweets_count * favorites_count * comments_count), 1/3)

        # Retrieve tweet text
        text_container = tweet_container.find_element_by_class_name("js-tweet-text-container")
        text_container_p = text_container.find_element_by_class_name("tweet-text")
        tweet_p = text_container_p.text
        
        # Example of dictionary for each tweet, and print
        tweet_dict = {
            "name": candidate["name"],
            "party": candidate["party"],
            "twitter_username": current_user,
            "stream_id": stream_id,
            "tweet_url": tweet_url,
            "unix_time": tweet["data_time"],
            "date_string": tweet_date_string,
            "datetime": tweet_date_datetime,
            "retweets": retweets_count,
            "favorites": favorites_count,
            "comments": comments_count,
            "engagement_score": engagement_score,
            "text": tweet_p
        }
        print(tweet_dict)
        
        # Append dictionary as a value to the "tweets" key for the candidate
        candidate["tweets"].append(
            {
                "name": candidate["name"],
                "party": candidate["party"],
                "twitter_username": current_user,
                "stream_id": stream_id,
                "tweet_url": tweet_url,
                "unix_time": tweet["data_time"],
                "date_string": tweet_date_string,
                "datetime": tweet_date_datetime,
                "retweets": retweets_count,
                "favorites": favorites_count,
                "comments": comments_count,
                "engagement_score": engagement_score,
                "text": tweet_p
            })




1
1
1
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1125529422205816834', 'tweet_url': 'https://twitter.com/JoeBiden/status/1125529422205816834', 'unix_time': 1557182100, 'date_string': '3:35 PM - 6 May 2019', 'datetime': datetime.datetime(2019, 5, 6, 15, 35), 'retweets': 940, 'favorites': 13685, 'comments': 255, 'engagement_score': 1485.8362350149803, 'text': 'Congratulations to the Duke and Duchess of Sussex, Prince Harry and Meghan Markle, on the birth of their baby boy! The truth is there’s no better job than being a parent. Jill and I wis

{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1124102681163960321', 'tweet_url': 'https://twitter.com/JoeBiden/status/1124102681163960321', 'unix_time': 1556841938, 'date_string': '5:05 PM - 2 May 2019', 'datetime': datetime.datetime(2019, 5, 2, 17, 5), 'retweets': 1837, 'favorites': 10726, 'comments': 312, 'engagement_score': 1831.894734390078, 'text': 'On Holocaust Remembrance Day, let us pause and reflect on the millions of Jews who lost their lives at the hands of the Nazi regime.\n\nThe events of the last few months remind us that it’s not enough to just say never again—we must speak up and act against hate.'}
{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1123995821962420225', 'tweet_url': 'https://twitter.com/JoeBiden/status/1123995821962420225', 'unix_time': 1556816461, 'date_string': '10:01 AM - 2 May 2019', 'datetime': datetime.datetime(2019, 5, 2, 10, 1), 'retweets': 952, 'favorites': 5307, 

{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1122977745699577857', 'tweet_url': 'https://twitter.com/JoeBiden/status/1122977745699577857', 'unix_time': 1556573733, 'date_string': '2:35 PM - 29 Apr 2019', 'datetime': datetime.datetime(2019, 4, 29, 14, 35), 'retweets': 119, 'favorites': 668, 'comments': 39, 'engagement_score': 145.81292107954334, 'text': 'By making post-secondary education and training affordable to and making sure the economy works not only for folks with a four-year degree but also for those who complete on-the-job training and trade programs, too.'}
{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1122977745049477126', 'tweet_url': 'https://twitter.com/JoeBiden/status/1122977745049477126', 'unix_time': 1556573732, 'date_string': '2:35 PM - 29 Apr 2019', 'datetime': datetime.datetime(2019, 4, 29, 14, 35), 'retweets': 95, 'favorites': 561, 'comments': 33, 'engagement_score': 120.70728141

{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1122153428627656705', 'tweet_url': 'https://twitter.com/JoeBiden/status/1122153428627656705', 'unix_time': 1556377200, 'date_string': '8:00 AM - 27 Apr 2019', 'datetime': datetime.datetime(2019, 4, 27, 8, 0), 'retweets': 1886, 'favorites': 14153, 'comments': 974, 'engagement_score': 2962.4410520106035, 'text': 'I have a message for #TeamJoe: Thank you!'}
{'name': 'Joe Biden', 'party': 'Democrat', 'twitter_username': 'JoeBiden', 'stream_id': '1121915023444590601', 'tweet_url': 'https://twitter.com/JoeBiden/status/1121915023444590601', 'unix_time': 1556320360, 'date_string': '4:12 PM - 26 Apr 2019', 'datetime': datetime.datetime(2019, 4, 26, 16, 12), 'retweets': 2422, 'favorites': 18209, 'comments': 1561, 'engagement_score': 4098.463256676473, 'text': "I had the privilege to thank one of our grassroots donors. It's because of supporters like Josh we're able to make this campaign a reality and bring t

running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running
running


...

{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1108468773558906882', 'tweet_url': 'https://twitter.com/AndrewYang/status/1108468773558906882', 'unix_time': 1553114524, 'date_string': '1:42 PM - 20 Mar 2019', 'datetime': datetime.datetime(2019, 3, 20, 13, 42), 'retweets': 346, 'favorites': 1557, 'comments': 128, 'engagement_score': 410.07021601308526, 'text': 'Depression among young people has skyrocketed https://www.businessinsider.com/depression-rates-by-age-young-people-2019-3 … we should take this very seriously and try to treat and strengthen from every angle @jean_twenge'}
{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1108458129333936134', 'tweet_url': 'https://twitter.com/AndrewYang/status/1108458129333936134', 'unix_time': 1553111986, 'date_string': '12:59 PM - 20 Mar 2019', 'datetime': datetime.datetime(2019, 3, 20, 12, 59), 'retweets': 95, 'favorites': 694, 'comments': 28, 'engagement_

{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1108185513645821952', 'tweet_url': 'https://twitter.com/AndrewYang/status/1108185513645821952', 'unix_time': 1553046990, 'date_string': '6:56 PM - 19 Mar 2019', 'datetime': datetime.datetime(2019, 3, 19, 18, 56), 'retweets': 788, 'favorites': 2901, 'comments': 199, 'engagement_score': 769.0873608464199, 'text': 'The Freedom Dividend is pro-work, not anti-work.  It will create more work in our economy and recognize the work that is already being done.'}
{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1108174785312370688', 'tweet_url': 'https://twitter.com/AndrewYang/status/1108174785312370688', 'unix_time': 1553044432, 'date_string': '6:13 PM - 19 Mar 2019', 'datetime': datetime.datetime(2019, 3, 19, 18, 13), 'retweets': 69, 'favorites': 1321, 'comments': 69, 'engagement_score': 184.58666913151828, 'text': 'My team is amazing - imagine having people w

{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1107976545484922881', 'tweet_url': 'https://twitter.com/AndrewYang/status/1107976545484922881', 'unix_time': 1552997168, 'date_string': '5:06 AM - 19 Mar 2019', 'datetime': datetime.datetime(2019, 3, 19, 5, 6), 'retweets': 319, 'favorites': 2588, 'comments': 494, 'engagement_score': 741.5844841200222, 'text': 'People are the answer not the problem.'}
{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1107965603267166208', 'tweet_url': 'https://twitter.com/AndrewYang/status/1107965603267166208', 'unix_time': 1552994559, 'date_string': '4:22 AM - 19 Mar 2019', 'datetime': datetime.datetime(2019, 3, 19, 4, 22), 'retweets': 96, 'favorites': 1017, 'comments': 37, 'engagement_score': 153.4374256439038, 'text': 'Over $1 million raised since Feb 12th!  Thank you for the incredible support!!  '}
{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'A

{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1107666913390444546', 'tweet_url': 'https://twitter.com/AndrewYang/status/1107666913390444546', 'unix_time': 1552923346, 'date_string': '8:35 AM - 18 Mar 2019', 'datetime': datetime.datetime(2019, 3, 18, 8, 35), 'retweets': 171, 'favorites': 808, 'comments': 47, 'engagement_score': 186.56712095992626, 'text': 'Interview with @NYMag http://nymag.com/intelligencer/2019/03/andrew-yang-is-more-than-a-meme.html … thanks @realaxelfoley '}
{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1107660268186812422', 'tweet_url': 'https://twitter.com/AndrewYang/status/1107660268186812422', 'unix_time': 1552921761, 'date_string': '8:09 AM - 18 Mar 2019', 'datetime': datetime.datetime(2019, 3, 18, 8, 9), 'retweets': 431, 'favorites': 2257, 'comments': 167, 'engagement_score': 545.642805772355, 'text': 'My appearance this morning on @Morning_Joe.  Yes, yes I do.'}
{'na

{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1107349821948608512', 'tweet_url': 'https://twitter.com/AndrewYang/status/1107349821948608512', 'unix_time': 1552847745, 'date_string': '11:35 AM - 17 Mar 2019', 'datetime': datetime.datetime(2019, 3, 17, 11, 35), 'retweets': 260, 'favorites': 1948, 'comments': 110, 'engagement_score': 381.9310749798362, 'text': 'We are going to have to do it ourselves.'}
{'name': 'Andrew Yang', 'party': 'Democrat', 'twitter_username': 'AndrewYang', 'stream_id': '1107346979611463680', 'tweet_url': 'https://twitter.com/AndrewYang/status/1107346979611463680', 'unix_time': 1552847068, 'date_string': '11:24 AM - 17 Mar 2019', 'datetime': datetime.datetime(2019, 3, 17, 11, 24), 'retweets': 2468, 'favorites': 12614, 'comments': 3131, 'engagement_score': 4602.145550966534, 'text': 'The problem with deciding Presidential elections via popular vote is that candidates would naturally campaign in urban areas with big medi

In [16]:
#Store all tweet lists into variables
Bidentweets = candidates_info[0]["tweets"]
Bookertweets = candidates_info[1]["tweets"]
Buttigiegtweets = candidates_info[2]["tweets"]
Castrotweets = candidates_info[3]["tweets"]
Delaneytweets = candidates_info[4]["tweets"]
Gabbardtweets = candidates_info[5]["tweets"]
Gillibrandtweets = candidates_info[6]["tweets"]
Graveltweets = candidates_info[7]["tweets"]
Harristweets = candidates_info[8]["tweets"]
Hickenloopertweets = candidates_info[9]["tweets"]
Insleetweets = candidates_info[10]["tweets"]
Klobuchartweets = candidates_info[11]["tweets"]
Messamtweets = candidates_info[12]["tweets"]
Moultontweets = candidates_info[13]["tweets"]
Rourketweets = candidates_info[14]["tweets"]
Ryantweets = candidates_info[15]["tweets"]
Sanderstweets = candidates_info[16]["tweets"]
Trumptweets = candidates_info[17]["tweets"]
Warrentweets = candidates_info[18]["tweets"]
Weldtweets = candidates_info[19]["tweets"]
Williamsontweets = candidates_info[20]["tweets"]
Yangtweets = candidates_info[21]["tweets"]



In [21]:
#Create dataframes for each candidates' tweets
Bidendf = pd.DataFrame(Bidentweets)
Bookerdf = pd.DataFrame(Bookertweets)
Buttigiegdf = pd.DataFrame(Buttigiegtweets)
Castrodf = pd.DataFrame(Castrotweets)
Delaneydf = pd.DataFrame(Delaneytweets)
Gabbarddf = pd.DataFrame(Gabbardtweets)
Gillibranddf = pd.DataFrame(Gillibrandtweets)
Graveldf = pd.DataFrame(Graveltweets)
Harrisdf = pd.DataFrame(Harristweets)
Hickenlooperdf = pd.DataFrame(Hickenloopertweets)
Insleedf = pd.DataFrame(Insleetweets)
Klobuchardf = pd.DataFrame(Klobuchartweets)
Messamdf = pd.DataFrame(Messamtweets)
Moultondf = pd.DataFrame(Moultontweets)
Rourkedf = pd.DataFrame(Rourketweets)
Ryandf = pd.DataFrame(Ryantweets)
Sandersdf = pd.DataFrame(Sanderstweets)
Trumpdf = pd.DataFrame(Trumptweets)
Warrendf = pd.DataFrame(Warrentweets)
Welddf = pd.DataFrame(Weldtweets)
Williamsondf = pd.DataFrame(Williamsontweets)
Yangdf = pd.DataFrame(Yangtweets)



In [23]:
#Combine all lists into one
all_tweets = Bidentweets\
    + Bookertweets\
    + Buttigiegtweets\
    + Castrotweets\
    + Delaneytweets\
    + Gabbardtweets\
    + Gillibrandtweets\
    + Graveltweets\
    + Harristweets\
    + Hickenloopertweets\
    + Insleetweets\
    + Klobuchartweets\
    + Messamtweets\
    + Moultontweets\
    + Rourketweets\
    + Ryantweets\
    + Sanderstweets\
    + Trumptweets\
    + Warrentweets\
    + Weldtweets\
    + Williamsontweets\
    + Yangtweets\



In [25]:
#Create combined dataframe
all_df = pd.DataFrame(all_tweets)


comments             date_string            datetime  engagement_score  \
0          255    3:35 PM - 6 May 2019 2019-05-06 15:35:00       1485.836235   
1          292    2:38 PM - 6 May 2019 2019-05-06 14:38:00        685.198576   
2          151    1:28 PM - 6 May 2019 2019-05-06 13:28:00        321.705558   
3          511    5:31 PM - 5 May 2019 2019-05-05 17:31:00       2371.390067   
4          521    4:17 PM - 5 May 2019 2019-05-05 16:17:00       1040.328735   
5          571   12:04 PM - 5 May 2019 2019-05-05 12:04:00       1377.759525   
6          142   10:46 AM - 5 May 2019 2019-05-05 10:46:00        391.124094   
7          168    9:54 AM - 5 May 2019 2019-05-05 09:54:00        319.612552   
8         2905    4:14 PM - 4 May 2019 2019-05-04 16:14:00       3719.835704   
9          224    2:46 PM - 4 May 2019 2019-05-04 14:46:00       1251.683834   
10         416   11:45 AM - 4 May 2019 2019-05-04 11:45:00        918.201363   
11         560    1:32 PM - 3 May 2019 2019-05-03 13:32:00        800.362752   
12         533    7:03 AM - 3 May 2019 2019-05-03 07:03:00       2191.147131   
13         312    5:05 PM - 2 May 2019 2019-05-02 17:05:00       1831.894734   
14         629   10:01 AM - 2 May 2019 2019-05-02 10:01:00       1470.208380   
15         331    8:33 AM - 2 May 2019 2019-05-02 08:33:00       1291.532856   
16         350    4:21 PM - 1 May 2019 2019-05-01 16:21:00       1402.731572   
17         476   10:52 AM - 1 May 2019 2019-05-01 10:52:00       2200.943600   
18        2394   3:25 PM - 30 Apr 2019 2019-04-30 15:25:00       4831.849215   
19         611   3:20 PM - 30 Apr 2019 2019-04-30 15:20:00       1368.012568   
20         343   2:55 PM - 30 Apr 2019 2019-04-30 14:55:00       1195.801372   
21         613   8:31 AM - 30 Apr 2019 2019-04-30 08:31:00       3193.418079   
22        3934   3:00 AM - 30 Apr 2019 2019-04-30 03:00:00       9768.923127   
23         311   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        682.742599   
24         188   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        672.602059   
25         106   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        299.620676   
26         117   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        319.634576   
27          39   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        145.812921   
28          33   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        120.707281   
29          46   2:35 PM - 29 Apr 2019 2019-04-29 14:35:00        211.242222   
...        ...                     ...                 ...               ...   
9624        98   1:51 PM - 18 Mar 2019 2019-03-18 13:51:00        391.120904   
9625        61  11:15 AM - 18 Mar 2019 2019-03-18 11:15:00        221.191115   
9626        54  10:11 AM - 18 Mar 2019 2019-03-18 10:11:00        152.401352   
9627        69   9:50 AM - 18 Mar 2019 2019-03-18 09:50:00        300.640498   
9628        47   8:35 AM - 18 Mar 2019 2019-03-18 08:35:00        186.567121   
9629       167   8:09 AM - 18 Mar 2019 2019-03-18 08:09:00        545.642806   
9630       195   6:44 AM - 18 Mar 2019 2019-03-18 06:44:00        643.282614   
9631       123   4:20 AM - 18 Mar 2019 2019-03-18 04:20:00        286.538165   
9632        37   4:15 AM - 18 Mar 2019 2019-03-18 04:15:00        113.121362   
9633        84   8:35 PM - 17 Mar 2019 2019-03-17 20:35:00        315.970341   
9634       712   8:28 PM - 17 Mar 2019 2019-03-17 20:28:00       1728.126327   
9635       150   8:10 PM - 17 Mar 2019 2019-03-17 20:10:00        422.413822   
9636       114   7:36 PM - 17 Mar 2019 2019-03-17 19:36:00        381.027919   
9637        86   5:42 PM - 17 Mar 2019 2019-03-17 17:42:00        183.484517   
9638       156   5:09 PM - 17 Mar 2019 2019-03-17 17:09:00        659.259031   
9639       531   4:55 PM - 17 Mar 2019 2019-03-17 16:55:00       1910.475575   
9640       100   3:09 PM - 17 Mar 2019 2019-03-17 15:09:00        291.867066   
9641       108   2:18 PM - 17 Mar 2019 2019-03-17 14:18:00        223.924826   
9642  

In [7]:
#Create connection to sqlite
engine = create_engine('sqlite:///../db/candidates_tweets.sqlite', echo = False)

In [8]:
#Export scraped data to sqlite
all_df.to_sql('candidates_tweets', con=engine, if_exists = 'replace', index = False)

NameError: name 'all_df' is not defined

In [82]:
#Check if data was read into sqlite
# engine.execute("SELECT * from candidates_tweets").fetchall()

In [96]:
conn = engine.connect()
# Create dataframe from database
candidate_df = pd.read_sql("SELECT * FROM candidates_tweets", conn)

In [84]:
candidate_df.head()

comments           date_string                    datetime  \
0       255  3:35 PM - 6 May 2019  2019-05-06 15:35:00.000000   
1       292  2:38 PM - 6 May 2019  2019-05-06 14:38:00.000000   
2       151  1:28 PM - 6 May 2019  2019-05-06 13:28:00.000000   
3       511  5:31 PM - 5 May 2019  2019-05-05 17:31:00.000000   
4       521  4:17 PM - 5 May 2019  2019-05-05 16:17:00.000000   

   engagement_score  favorites       name     party  retweets  \
0       1485.836235      13685  Joe Biden  Democrat       940   
1        685.198576       2727  Joe Biden  Democrat       404   
2        321.705558       1045  Joe Biden  Democrat       211   
3       2371.390067      14870  Joe Biden  Democrat      1755   
4       1040.328735       3626  Joe Biden  Democrat       596   

             stream_id                                               text  \
0  1125529422205816834  Congratulations to the Duke and Duchess of Sus...   
1  1125515077564502016  On Saturday, Jill and I visited Columbia, Sout...   
2  1125497461785616386  Nevada, we’re taking our campaign to Henderson...   
3  1125196320816467969  On this first day of Ramadan, Jill and I wish ...   
4  1125177603780825089  Our country may seem more divided than ever, b...   

                                           tweet_url twitter_username  \
0  https://twitter.com/JoeBiden/status/1125529422...         JoeBiden   
1  https://twitter.com/JoeBiden/status/1125515077...         JoeBiden   
2  https://twitter.com/JoeBiden/status/1125497461...         JoeBiden   
3  https://twitter.com/JoeBiden/status/1125196320...         JoeBiden   
4  https://twitter.com/JoeBiden/status/1125177603...         JoeBiden   

    unix_time  
0  1557182100  
1  1557178680  
2  1557174480  
3  1557102682  
4  1557098220

In [44]:
# candidate_df.count()
len(candidate_df)

9654

In [133]:
#Filter for tweets which have more than 30 comments
candidate_filtered_df = candidate_df.loc[candidate_df["comments"] > 30, :]

# Retrieve names from filtered dataframe
candidate_names = candidate_filtered_df["name"].unique()

#Iterate through names 
for name in candidate_names:
    name_df = candidate_filtered_df.loc[candidate_filtered_df["name"] == name,:]
    # Filter the dataframe further if the candidate does not have more than 100 tweets
    if len(name_df) < 100:
        candidate_filtered_df = candidate_filtered_df.loc[candidate_filtered_df["name"] != name,:]
        
#Store in a new dataframe
new_filtered_df = candidate_filtered_df
print(len(new_filtered_df))
new_filtered_df["name"].value_counts()

5967


Kamala Harris         767
Elizabeth Warren      671
Bernie Sanders        612
Andrew Yang           567
Donald Trump          545
Tulsi Gabbard         479
Cory Booker           466
Beto O'Rourke         431
Amy Klobuchar         422
Kirsten Gillibrand    317
Pete Buttigieg        256
Jay Inslee            193
Julián Castro         139
Mike Gravel           102
Name: name, dtype: int64

In [135]:
# Create list to store the top 5 candidates
top_candidates = []

#Retrieve names from filtered list
filtered_names = new_filtered_df["name"].unique()

#Itereate through names
for i in filtered_names:
    candidate_name = i
    
    #Find the median engagement score for each candidate
    #Note this is after the original data has been filtered, does not reflect "true" median
    #We only want to retrieve an arbitrary 5 candidates. May wish to revisit this portion of the method
    filtered_name_df = new_filtered_df.loc[new_filtered_df["name"] == i,:]
    candidate_engagement_average = filtered_name_df["engagement_score"].median()
    
    top_candidates.append({
        "name": i,
        "average_engagement_score": candidate_engagement_average
    })

#Sort list by top engagement scores and slice for the top 5
print(top_candidates)
top_candidates.sort(key = lambda x:x["average_engagement_score"], reverse = True)
top_candidates = top_candidates[:5]
print(top_candidates)
print(len(top_candidates))


[{'name': 'Cory Booker', 'average_engagement_score': 368.6468532555268}, {'name': 'Pete Buttigieg', 'average_engagement_score': 1509.4967224947197}, {'name': 'Julián Castro', 'average_engagement_score': 313.887906761864}, {'name': 'Tulsi Gabbard', 'average_engagement_score': 621.0782848833343}, {'name': 'Kirsten Gillibrand', 'average_engagement_score': 204.90467112429633}, {'name': 'Mike Gravel', 'average_engagement_score': 417.3445494281961}, {'name': 'Kamala Harris', 'average_engagement_score': 1732.8701347446226}, {'name': 'Jay Inslee', 'average_engagement_score': 135.40309334039412}, {'name': 'Amy Klobuchar', 'average_engagement_score': 451.6409339449649}, {'name': "Beto O'Rourke", 'average_engagement_score': 512.9562449144296}, {'name': 'Bernie Sanders', 'average_engagement_score': 1489.2372284104858}, {'name': 'Donald Trump', 'average_engagement_score': 29689.34015553014}, {'name': 'Elizabeth Warren', 'average_engagement_score': 603.1160116605478}, {'name': 'Andrew Yang', 'averag

In [149]:
#Scrape replies from random tweets

top_names = [x["name"] for x in top_candidates]

# Create list to append texts from replies to candidates' tweets
top_candidates_replies = []
for j in top_names:
    # Find 100 random tweets from candidate
    top_candidate_df = new_filtered_df.loc[new_filtered_df["name"] == j,:]
    candidate_length = len(top_candidate_df)
    random_list = numpy.random.choice(candidate_length, 100, replace = False)
    
    for k in random_list:
        #locate the row of random index
        current_row = top_candidate_df.iloc[k,:]
        
        # Retrieve username for filtering purposes
        k_username = current_row["twitter_username"]
        
        # Retrieve tweet ur
        current_top_tweet = current_row["tweet_url"]
        # Selenium get url
        driver.get(current_top_tweet)
        
        # Find all reply tweets
        replies_div = driver.find_element_by_class_name("replies-to")
        tweets_replies = replies_div.find_elements_by_class_name("tweet")
        
        #Create list to append replies which aren't from the current user
        filtered_tweets = []
        #Iterate through reply tweets
        # Note: this is not a representative sample of tweet replies. It will only generate
        # replies which first load, not any tweets which require scrolling. This will cause a
        # large selection bias. Furthermore, there will be many instances in which a single
        # user is represented many times across many tweets or even within the replies of a 
        # single tweet. This is due to twitter's algorithm. This section would be worth revisiting
        # to obtain a more representative sample. However, it is worth noting that the top replies
        # to a tweet are probably pushed there by twitter's algorithm because of their high
        # engagement numbers i.e. many people agree with the sentiment of the tweet. So, the
        # selection bias may not be as large as it first appears
        for tweet in tweets_replies:
            tweet_username_text = tweet.find_element_by_class_name("username").text
            if tweet_username_text[1:] == k_username:
                continue
            filtered_tweets.append(tweet)
        
        #Iterate through filtered tweets
        for x in filtered_tweets:
            filtered_text = x.find_element_by_class_name("js-tweet-text").text
            top_candidates_replies.append({
                "name": current_row["name"],
                "engagement_score": current_row["engagement_score"],
                "stream_id": current_row["stream_id"],
                "tweet_url": current_row["tweet_url"],
                "reply_text": filtered_text
            })
print(top_candidates_replies)


[{'name': 'Donald Trump', 'engagement_score': 23060.25589167694, 'stream_id': '1121829933679042565', 'tweet_url': 'https://twitter.com/realDonaldTrump/status/1121829933679042565', 'reply_text': '“Trump is the most dishonest president ever.” — cheif honesty expert, USA'}, {'name': 'Donald Trump', 'engagement_score': 23060.25589167694, 'stream_id': '1121829933679042565', 'tweet_url': 'https://twitter.com/realDonaldTrump/status/1121829933679042565', 'reply_text': "I wonder if Trump will be named the 'Cheif Mass Shooting Expert, NRA'"}, {'name': 'Donald Trump', 'engagement_score': 23060.25589167694, 'stream_id': '1121829933679042565', 'tweet_url': 'https://twitter.com/realDonaldTrump/status/1121829933679042565', 'reply_text': 'Instead of having meetings with the NRA, he should be calling for the termination of the NRA.'}, {'name': 'Donald Trump', 'engagement_score': 23060.25589167694, 'stream_id': '1121829933679042565', 'tweet_url': 'https://twitter.com/realDonaldTrump/status/1121829933679

In [150]:
#Create dataframe from scraped replies
all_replies_df = pd.DataFrame(top_candidates_replies)

In [152]:
all_replies_df.head()

engagement_score          name  \
0      23060.255892  Donald Trump   
1      23060.255892  Donald Trump   
2      23060.255892  Donald Trump   
3      23060.255892  Donald Trump   
4      23060.255892  Donald Trump   

                                          reply_text            stream_id  \
0  “Trump is the most dishonest president ever.” ...  1121829933679042565   
1  I wonder if Trump will be named the 'Cheif Mas...  1121829933679042565   
2  Instead of having meetings with the NRA, he sh...  1121829933679042565   
3  Yeah. Let's terminate a lobbyist group that ho...  1121829933679042565   
4  Did you ask them about the Russian Agent, who ...  1121829933679042565   

                                           tweet_url  
0  https://twitter.com/realDonaldTrump/status/112...  
1  https://twitter.com/realDonaldTrump/status/112...  
2  https://twitter.com/realDonaldTrump/status/112...  
3  https://twitter.com/realDonaldTrump/status/112...  
4  https://twitter.com/realDonaldTrump/status/112...

In [153]:
print(len(all_replies_df))

9202


In [154]:
all_replies_df.dropna(how = "any")

engagement_score           name  \
0         23060.255892   Donald Trump   
1         23060.255892   Donald Trump   
2         23060.255892   Donald Trump   
3         23060.255892   Donald Trump   
4         23060.255892   Donald Trump   
5         23060.255892   Donald Trump   
6         23060.255892   Donald Trump   
7         23060.255892   Donald Trump   
8         23060.255892   Donald Trump   
9         23060.255892   Donald Trump   
10        23060.255892   Donald Trump   
11        23060.255892   Donald Trump   
12        23060.255892   Donald Trump   
13        23060.255892   Donald Trump   
14        23060.255892   Donald Trump   
15        23060.255892   Donald Trump   
16        23060.255892   Donald Trump   
17        23060.255892   Donald Trump   
18        23060.255892   Donald Trump   
19        23060.255892   Donald Trump   
20         8903.741993   Donald Trump   
21         8903.741993   Donald Trump   
22         8903.741993   Donald Trump   
23         8903.741993   Donald Trump   
24         8903.741993   Donald Trump   
25         8903.741993   Donald Trump   
26         8903.741993   Donald Trump   
27         8903.741993   Donald Trump   
28         8903.741993   Donald Trump   
29         8903.741993   Donald Trump   
...                ...            ...   
9172        210.815874  Tulsi Gabbard   
9173        210.815874  Tulsi Gabbard   
9174        210.815874  Tulsi Gabbard   
9175        210.815874  Tulsi Gabbard   
9176        210.815874  Tulsi Gabbard   
9177        210.815874  Tulsi Gabbard   
9178        210.815874  Tulsi Gabbard   
9179        210.815874  Tulsi Gabbard   
9180        210.815874  Tulsi Gabbard   
9181        210.815874  Tulsi Gabbard   
9182        375.013973  Tulsi Gabbard   
9183        375.013973  Tulsi Gabbard   
9184        375.013973  Tulsi Gabbard   
9185        375.013973  Tulsi Gabbard   
9186        375.013973  Tulsi Gabbard   
9187        375.013973  Tulsi Gabbard   
9188        375.013973  Tulsi Gabbard   
9189        375.013973  Tulsi Gabbard   
9190        375.013973  Tulsi Gabbard   
9191        375.013973  Tulsi Gabbard   
9192        375.013973  Tulsi Gabbard   
9193        375.013973  Tulsi Gabbard   
9194        375.013973  Tulsi Gabbard   
9195        375.013973  Tulsi Gabbard   
9196        375.013973  Tulsi Gabbard   
9197        375.013973  Tulsi Gabbard   
9198        375.013973  Tulsi Gabbard   
9199        375.013973  Tulsi Gabbard   
9200        375.013973  Tulsi Gabbard   
9201        375.013973  Tulsi Gabbard   

                                             reply_text            stream_id  \
0     “Trump is the most dishonest president ever.” ...  1121829933679042565   
1     I wonder if Trump will be named the 'Cheif Mas...  1121829933679042565   
2     Instead of having meetings with the NRA, he sh...  1121829933679042565   
3     Yeah. Let's terminate a lobbyist group that ho...  1121829933679042565   
4     Did you ask them about the Russian Agent, who ...  1121829933679042565   
5                He probably asked them to do it again.  1121829933679042565   
6     The NRA gave $30Million to the 2016 Trump camp...  1121829933679042565   
7                            THANK YOU PRESIDENT TRUMP!  1121829933679042565   
8                                   NEVER FORGET! #MAGA  1121829933679042565   
9                              #RestartMIGA #MIGA #MAGA  1121829933679042565   
10                                        #maga \n#miga  1121829933679042565   
11      #Media4RestartLeader \n#Seyed_Mohammad_Hosseini  1121829933679042565   
12    How Much Did The NRA Spend On Getting Trump El...  1121829933679042565   
13    Six in 10 Americans Support Stricter Gun Laws ...  1121829933679042565   
14    4 things Donald Trump is doing to loosen gun l...  1121829933679042565   
15    With Trump and @GOP, it's just more lies and M...  1121829933679042565   
16    Since Parkland: 12 Months. 1,200 Kids Killed b...  1121829933679042565   
17    New CDC data show

In [156]:
print(len(all_replies_df))

9202


In [157]:
#Create connection to sqlite
reply_engine = create_engine('sqlite:///../db/candidates_tweets_replies.sqlite', echo = False)

In [158]:
#Export scraped data to sqlite
all_replies_df.to_sql('candidates_tweets_replies', con=reply_engine, if_exists = 'replace', index = False)

In [159]:
#Check if data was read into sqlite
reply_engine.execute("SELECT * from candidates_tweets_replies").fetchall()

[(23060.25589167694, 'Donald Trump', '“Trump is the most dishonest president ever.” — cheif honesty expert, USA', '1121829933679042565', 'https://twitter.com/realDonaldTrump/status/1121829933679042565'),
 (23060.25589167694, 'Donald Trump', "I wonder if Trump will be named the 'Cheif Mass Shooting Expert, NRA'", '1121829933679042565', 'https://twitter.com/realDonaldTrump/status/1121829933679042565'),
 (23060.25589167694, 'Donald Trump', 'Instead of having meetings with the NRA, he should be calling for the termination of the NRA.', '1121829933679042565', 'https://twitter.com/realDonaldTrump/status/1121829933679042565'),
 (23060.25589167694, 'Donald Trump', "Yeah. Let's terminate a lobbyist group that holds politicians accountable because you disagree with them?\n\nThank God for the NRA and ALCU.  Our first and second amendment rights wouldn't exist without them. Want no guns? Go move to Europe", '1121829933679042565', 'https://twitter.com/realDonaldTrump/status/1121829933679042565'),
 

In [160]:
#Export all reply data to csv
export_replies_csv = all_replies_df.to_csv("../datasets/candidates_tweets_replies.csv", index = None, header = True, encoding = 'utf-8-sig')

In [35]:
#Export all tweets data to csv
export_csv = all_df.to_csv("datasets/candidates_tweets.csv", index = None, header = True, encoding = 'utf-8-sig')